|  Sunrise logo | ![EEW logo](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/eew.jpg?raw=true) | ![EDGI logo](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/edgi.png?raw=true) |
|---|---|---|

#### This notebook is licensed under GPL 3.0. Please visit our Github repo for more information: https://github.com/edgi-govdata-archiving/ECHO-COVID19
#### The notebook was collaboratively authored by EDGI following our authorship protocol: https://docs.google.com/document/d/1CtDN5ZZ4Zv70fHiBTmWkDJ9mswEipX6eCYrwicP66Xw/
#### For more information about this project, visit https://www.environmentalenforcementwatch.org/

## How to Run
* A "cell" in a Jupyter notebook is a block of code performing a set of actions making available or using specific data.  The notebook works by running one cell after another, as the notebook user selects offered options.
* If you click on a gray **code** cell, a little “play button” arrow appears on the left. If you click the play button, it will run the code in that cell (“**running** a cell”). The button will animate. When the animation stops, the cell has finished running.
![Where to click to run the cell](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/pressplay.JPG?raw=true)
* You may get a warning that the notebook was not authored by Google. We know, we authored them! It’s okay. Click “Run Anyway” to continue. 
![Error Message](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/warning-message.JPG?raw=true)
* **It is important to run cells in order because they depend on each other.**
* Run all of the cells in a Notebook to make a complete report. Please feel free to look at and **learn about each result as you create it**!

# **Let's begin!** 
These first two cells give us access to some external Python code we will need. Hover over the "[ ]" on the top left corner of the cell below and you should see a "play" button appear. Click on it to run the cell then move to the next one.
### 1.  Bring in some code that is stored in a Github project.

In [73]:
!git clone https://github.com/edgi-govdata-archiving/ECHO_modules.git
!git clone https://github.com/edgi-govdata-archiving/ECHO-Geo.git
!git clone -b first-draft --single-branch  https://github.com/edgi-govdata-archiving/ECHO-Sunrise.git # This has the utilities file for mapping

Cloning into 'ECHO_modules'...
remote: Enumerating objects: 27, done.
remote: Counting objects: 100% (27/27), done.
remote: Compressing objects: 100% (21/21), done.
remote: Total 27 (delta 7), reused 16 (delta 4), pack-reused 0
Unpacking objects: 100% (27/27), done.
Cloning into 'ECHO-Geo'...
remote: Enumerating objects: 11, done.
remote: Counting objects: 100% (11/11), done.
remote: Compressing objects: 100% (8/8), done.
remote: Total 11 (delta 2), reused 6 (delta 2), pack-reused 0
Unpacking objects: 100% (11/11), done.
Cloning into 'ECHO-Sunrise'...
remote: Enumerating objects: 164, done.
remote: Counting objects: 100% (164/164), done.
remote: Compressing objects: 100% (152/152), done.
remote: Total 164 (delta 62), reused 87 (delta 11), pack-reused 0
Receiving objects: 100% (164/164), 8.79 MiB | 1.92 MiB/s, done.
Resolving deltas: 100% (62/62), done.


### 2.  Run some external Python modules.

In [74]:
# Import code libraries
%run ECHO_modules/DataSet.py
%run utilities.py #ECHO-Sunrise/
import urllib.parse
import pandas as pd
!pip install geopandas
import geopandas
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import requests
import csv
import datetime
import ipywidgets as widgets

You should consider upgrading via the '/Users/Eric/anaconda3/bin/python -m pip install --upgrade pip' command.


### 3. What facilities does EPA track in Mass?
This may take just a little bit of time to load - there are thousands!

In [75]:
echo_data_sql = "select * from ECHO_EXPORTER where FAC_STATE = 'MA' and FAC_ACTIVE_FLAG='Y'" # and GHG_FLAG='Y'" # 24000 facilities in total, but can we load them all?

try:
    print(echo_data_sql)
    echo_data = get_data( echo_data_sql, 'REGISTRY_ID' )
    num_facilities = echo_data.shape[0]
    print("\nThere are %s facilities in Massachussets currently tracked in the ECHO database." %(num_facilities))
except pd.errors.EmptyDataError:
    print("\nThere are no facilities in this region.\n")

select * from ECHO_EXPORTER where FAC_STATE = 'MA' and FAC_ACTIVE_FLAG='Y'


/Users/Eric/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3254: DtypeWarning: Columns (5,119) have mixed types. Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):



There are 24226 facilities in Massachussets currently tracked in the ECHO database.


In [23]:
%run utilities.py

In [76]:
mapper_marker(echo_data)

### 4.  Run this next cell to create to choose how you want to *zoom in*: what specific programs you want to look at and whether you want to view this information by county, congressional district or zip code.
Here's where you can learn more about the different programs...

In [77]:
%run ECHO_modules/make_data_sets.py

# Only list the data set if it has the correct flag set.
data_set_choices = []
for k, v in data_sets.items():
    if ( v.has_echo_flag( echo_data ) ):
        data_set_choices.append( k )

data_set_widget=widgets.Dropdown(
    options=list(data_set_choices),
    description='Data sets:',
    disabled=False,
    value='Greenhouse Gases'
) 
display(data_set_widget)

region_field = { 
    'Congressional District': { "field": "cd" },
    'County': { "field": "county" },
    'Town': {"field": "town"},
    'Watershed': {"field": "watershed"},
    'Zip Code': { "field": "zip" },
}

style = {'description_width': 'initial'}
select_region_widget = widgets.Dropdown(
    options=region_field.keys(),
    style=style,
    value='County',
    description='Region of interest:',
    disabled=False
)
display( select_region_widget )

Dropdown(description='Data sets:', index=9, options=('RCRA Violations', 'RCRA Inspections', 'RCRA Enforcements…

Dropdown(description='Region of interest:', index=1, options=('Congressional District', 'County', 'Town', 'Wat…

### 5. Here are all the facilities in this program
This may take some time because we're looking at all incidents for all facilities across the state!

In [87]:
program = data_sets[ data_set_widget.value ]
program_data = None
key=dict() # Create a way to look up Registry IDs in ECHO_EXPORTER later

# We need to provide a custom list of program ids for some programs.
if ( program.name == "Air Inspections" or program.name == "Air Enforcements" ):
    # The REGISTRY_ID field is the index of the echo_data
    registry_ids = echo_data[echo_data['AIR_FLAG'] == 'Y'].index.values
    key = { i : i for i in registry_ids }
    program_data = program.get_data( ee_ids=registry_ids )
elif ( program.name == "Combined Air Emissions" ):
    ghg_registry_ids = echo_data[echo_data['GHG_FLAG'] == 'Y'].index.values
    tri_registry_ids = echo_data[echo_data['TRI_FLAG'] == 'Y'].index.values
    id_set = np.union1d( ghg_registry_ids, tri_registry_ids )
    registry_ids = list(id_set)
    program_data = program.get_data( ee_ids=registry_ids )
    key = { i : i for i in registry_ids }
elif ( program.name == "Greenhouse Gases" or program.name == "Toxic Releases" ):
    program_flag = program.echo_type + '_FLAG'
    registry_ids = echo_data[echo_data[ program_flag ] == 'Y'].index.values
    program_data = program.get_data( ee_ids=registry_ids )
    key = { i : i for i in registry_ids }
else:
    ids_string = program.echo_type + '_IDS'
    ids = list()
    registry_ids = list()
    for index, value in echo_data[ ids_string ].items():
        try:
            for this_id in value.split():
                ids.append( this_id )
                key[this_id]=index
        except ( KeyError, AttributeError ) as e:
            pass
    program_data = program.get_data( ee_ids=ids )

# Find the facility that matches the program data, by REGISTRY_ID.  
# Add lat and lon, facility name and REGISTRY_ID as fac_registry_id. 
# (Note: not adding REGISTRY_ID right now as it is sometimes interpreted as an int and that messes with the charts...)
my_prog_data = pd.DataFrame()
no_data_ids = []

# Look through all the facilities in my area and program and get supplemental echo_data info
if (program_data is None): # Handle no data
    print("Sorry, we don't have data for this program! That could be an error on our part, or ECHO's, or because the data type doesn't apply to this area.")
else:
    for fac in program_data.itertuples():
        fac_id = fac.Index
        reg_id = key[fac_id] # Look up this facility's Registry ID through its Program ID
        try:
            echo_row = pd.DataFrame(echo_data.loc[reg_id].copy()).T.reset_index() # Find and filter to the corresponding row in ECHO_EXPORTER
            echo_row = echo_row[['FAC_NAME', 'FAC_LAT', 'FAC_LONG']] # Keep only the columns we need
            program_row =  pd.DataFrame([list(fac)[1:]], columns=program_data.columns.values) # Turn the program_data tuple into a DataFrame
            full_row = pd.concat([program_row, echo_row], axis=1) # Join the EE row df and the program row df
            frames = [my_prog_data, full_row]
            my_prog_data = pd.concat( frames, ignore_index=False)
        except KeyError:
            # The facility wasn't found in the program data.
            no_data_ids.append( fac.Index )

my_prog_data

...
...
...
Sorry, we don't have data for this program! That could be an error on our part, or ECHO's, or because the data type doesn't apply to this area.


Empty DataFrame
Columns: []
Index: []

In [96]:
registry_ids

array([1.10000310e+11, 1.10000882e+11, 1.10001950e+11, 1.10009023e+11,
       1.10031010e+11, 1.10000312e+11, 1.10025248e+11, 1.10024371e+11,
       1.10012199e+11, 1.10024371e+11, 1.10001263e+11, 1.10008420e+11,
       1.10000310e+11, 1.10009586e+11, 1.10024339e+11, 1.10024808e+11,
       1.10000309e+11, 1.10024352e+11, 1.10002018e+11, 1.10000740e+11,
       1.10001948e+11, 1.10000308e+11, 1.10024371e+11, 1.10000310e+11,
       1.10000309e+11, 1.10000308e+11, 1.10011137e+11, 1.10002029e+11,
       1.10023149e+11, 1.10000309e+11, 1.10012166e+11, 1.10002012e+11,
       1.10001938e+11, 1.10000312e+11, 1.10001938e+11, 1.10010426e+11,
       1.10000835e+11, 1.10000311e+11, 1.10001959e+11, 1.10000310e+11,
       1.10000603e+11, 1.10000308e+11, 1.10024357e+11, 1.10000847e+11,
       1.10024376e+11, 1.10002001e+11, 1.10001944e+11, 1.10038499e+11,
       1.10000835e+11, 1.10001950e+11, 1.10000310e+11, 1.10021141e+11,
       1.10000309e+11, 1.10043812e+11, 1.10002062e+11, 1.10040448e+11,
      

In [67]:
# in ordert to map, roll up my_prog_data to facility level
fac = my_prog_data.drop_duplicates(subset=['FAC_NAME']) # easy, but not necessarily accurate key
map_of_facilities = mapper_marker(fac)
map_of_facilities

KeyError: Index(['NPDES_ID'], dtype='object')

### 6. Here are the geographies we're going to summarize this information at

In [52]:
# read in and map geojson for the selected geography
geo = region_field[select_region_widget.value]["field"].lower()
geo_json_data = geopandas.read_file("ECHO-Geo/ma_"+geo+".geojson")

m = folium.Map(
    #tiles='Mapbox Bright',
)
folium.GeoJson(
    geo_json_data,
).add_to(m)

bounds = m.get_bounds()
m.fit_bounds(bounds)

m

Dropdown(description='Region of interest:', index=1, options=('Congressional District', 'County', 'Town', 'Watershed', 'Zip Code'), style=DescriptionStyle(description_width='initial'), value='County')


### 7. Now we bring the geographic data and the facility data together. First, let's rank each geography.

In [57]:
# first, spatialize my_prog_data
gdf = geopandas.GeoDataFrame(
    my_prog_data, geometry=geopandas.points_from_xy(my_prog_data["FAC_LONG"], my_prog_data["FAC_LAT"]))

join = geopandas.sjoin(gdf, geo_json_data, how="inner", op='intersects')

# get geo and attribute data column names
geo_column = {"county": "COUNTY"} # EXPAND
att_column = {"Greenhouse Gases": {"col":"ANNUAL_EMISSION", "agg":"sum"}, 
              "Clean Water Inspections": {"col":"ACTIVITY_TYPE_CODE", "agg":"count"}} # EXPAND
g = geo_column[geo]
a = att_column[program.name]["col"]

test = join.groupby(join[g])[[a]].agg(att_column[program.name]["agg"])
test.sort_values(by=a, ascending = False)

/Users/Eric/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:4326

  """


ACTIVITY_TYPE_CODE
COUNTY                        
WORCESTER                 1061
MIDDLESEX                  848
FRANKLIN                   824
ESSEX                      677
BERKSHIRE                  497
BRISTOL                    495
HAMPDEN                    493
HAMPSHIRE                  386
NORFOLK                    267
PLYMOUTH                   253
SUFFOLK                    156
BARNSTABLE                  26
DUKES                        4

### 8. Now, let's map it!

In [58]:
test.reset_index(inplace=True)
att_data = test.rename(columns={g: "geo", a: "value"}) 
mp = mapper_area(geo_json_data, att_data, g)
mp

### 9. Rank individual facilities

In [62]:
ranked = my_prog_data.groupby(["FAC_NAME", "FAC_LAT", "FAC_LONG"])[[a]].agg("sum")
ranked.reset_index(inplace=True)
ranked = ranked.set_index("FAC_NAME")
ranked.sort_values(by=a, ascending=False)

FAC_LAT   FAC_LONG  \
FAC_NAME                                                                   
FALL RIVER REGIONAL WASTEWATER TREATMENT FACILITY   41.677757 -71.195583   
REGIONAL WASTEWATER TREATMENT FACILITY              42.648304 -71.288911   
ERVING WASTEWATER TREATMENT PLANT #2                42.597500 -72.387900   
SPRINGFIELD REGIONAL WASTEWATER TREATMENT PLANT     42.087793 -72.588998   
WESTBOROUGH WASTEWATER TREATMENT PLANT              42.280190 -71.632480   
AMESBURY WATER POLLUTION ABATEMENT PLANT            42.840524 -70.926953   
NEW BEDFORD WASTEWATER TREATMENT FACILITY           41.595387 -70.905558   
CHICOPEE WATER POLLUTION CONTROL                    42.153760 -72.621660   
MONTAGUE WASTEWATER TREATMENT FACILITY              42.580800 -72.572320   
NEWBURYPORT WASTEWATER TREATMENT FACILITY           42.809271 -70.861505   
NORTHAMPTON WASTEWATER TREATMENT PLANT              42.313056 -72.623333   
GREAT BARRINGTON WASTEWATER TREATMENT FACILITY      42.189940 -73.357090   
EASTHAMPTON WASTEWATER TREATMENT PLANT              42.277698 -72.648897   
BROCKTON ADVANCED WATER RECLAMATION FAC             42.049280 -71.002800   
PALMER WATER POLLUTION CONTROL FACILITY             42.185311 -72.362228   
SOUTH DEERFIELD WASTEWATER TREATMENT PLANT          42.468290 -72.589140   
LEOMINSTER WASTEWATER TREATMENT FACILITY            42.521522 -71.739264   
SOUTH HADLEY WASTEWATER TREATMENT FACILITY          42.205371 -72.588140   
FITCHBURG EAST WASTEWATER TREATMENT FACILITY        42.543505 -71.747368   
IPSWICH WASTEWATER TREATMENT PLANT                  42.691174 -70.838884   
WARE WASTEWATER TREATMENT PLANT                     42.251940 -72.255140   
NORTH ATTLEBOROUGH WASTEWATER TREATMENT FACILITY    41.960640 -71.306250   
HOOSIC WASTWATER TREAMENT PLANT                     42.729594 -73.211578   
GREENFIELD WATER POLLUTION CONTROL FACILITY         42.571367 -72.598121   
WEBSTER WASTWATER TREATMENT FACILITY                42.038576 -71.888022   
GLOUCESTER WASTEWATER TREATMENT FACILITY\t          42.611338 -70.680381   
CHARLES RIVER WASTEWATER TREATMENT FACILITY         42.140870 -71.388960   
ADAMS WASTEWATER TREATMENT PLANT                    42.644677 -73.108628   
SOUTH ESSEX WASTEWATER TREATMENT PLANT              42.535831 -70.836397   
MWRA CLINTON WASTEWATER TREATMENT PLANT             42.430960 -71.680824   
...                                                       ...        ...   
GARDNER CITY HALL TOWN OF                           42.574130 -71.995380   
GRANITE STATE CONCRETE                              42.626340 -71.418780   
GREENWOOD II                                        42.358500 -71.849600   
GRISTMILL VILLAGE                                   42.188360 -71.702040   
GUTIERREZ COMPANY                                   42.627685 -71.366076   
HAMPDEN PAPERS INC                                  42.198020 -72.600910   
HANSCOM AIR FORCE BASE                              42.470666 -71.289444   
HARTFORD VILLAGE PHASE II                           42.114500 -71.478300   
HERO COATINGS                                       42.801470 -70.893470   
HIGH POINT                                          42.169703 -71.179875   
HINGHAM SHIPYARD MARINA                             42.252540 -70.920540   
HINGHAM STREET WATER TREATMENT PLANT                42.159322 -70.903260   
HOLLISTON TRANSFER STATION                          42.216680 -71.413360   
IDEAL TAPE COMPANY                                  42.638280 -71.342290   
LEWCOTT CORPORATION                                 42.185680 -71.744190   
INSCO                                               42.617350 -71.583020   
INTEL FAB 17 SEMICONDUCTOR MANUFACTURING            42.379380 -71.556960   
IRON HORSE PARK OPERATIONS CONTRL CENTER  MBTA ...  42.585100 -71.264300   
JILLIAN'S LANE                                      42.412720 -71.550820   
JOHNSON MATTHEY PHARMA SERVICES                     42.528806 -71.625768   
KANE PERKINS CONSTRUCTION 

### 10. Map individual facilities

In [65]:
ranked['quantile'] = pd.qcut(ranked[a], 4, labels=False, duplicates="drop")
mp = mapper_circle(ranked, a)
mp

KeyError: 'FAC_NAME'